### Common friends

In [1]:
from pyspark import SparkContext
sc = SparkContext()

25/04/04 13:58:06 WARN Utils: Your hostname, mbds resolves to a loopback address: 127.0.1.1; using 57.128.107.207 instead (on interface ens3)
25/04/04 13:58:06 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4042. Attempting port 4043.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4043. Attempting port 4044.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4044. Attempting port 4045.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI' could not bind on port 4045. Attempting port 4046.
25/04/04 13:58:07 WARN Utils: Service 'SparkUI

In [2]:
!hadoop fs -put /vagrant/tp/3/friends.txt

put: `friends.txt': File exists


In [3]:
data = sc.textFile("friends.txt")
data.collect()

['A=>B,C,D', 'B=>A,C,D,E', 'C=>A,B,D,E', 'D=>A,B,C,E', 'E=>B,C,D']

In [4]:
splitted = data.map(lambda x: x.split("=>"))
splitted.collect()

[['A', 'B,C,D'],
 ['B', 'A,C,D,E'],
 ['C', 'A,B,D,E'],
 ['D', 'A,B,C,E'],
 ['E', 'B,C,D']]

In [5]:
listed = splitted.mapValues(lambda x: x.split(","))
listed.collect()

[('A', ['B', 'C', 'D']),
 ('B', ['A', 'C', 'D', 'E']),
 ('C', ['A', 'B', 'D', 'E']),
 ('D', ['A', 'B', 'C', 'E']),
 ('E', ['B', 'C', 'D'])]

In [6]:
def amis(couple):
    """Prend un couple amis et liste et renvoie les couple A-B"""
    clefs = [couple[0]+ i for i in couple[1]]
    return [("-".join(sorted(i)), couple[1]) for i in clefs]

In [7]:
mapped = listed.flatMap(amis)
mapped.collect()

[('A-B', ['B', 'C', 'D']),
 ('A-C', ['B', 'C', 'D']),
 ('A-D', ['B', 'C', 'D']),
 ('A-B', ['A', 'C', 'D', 'E']),
 ('B-C', ['A', 'C', 'D', 'E']),
 ('B-D', ['A', 'C', 'D', 'E']),
 ('B-E', ['A', 'C', 'D', 'E']),
 ('A-C', ['A', 'B', 'D', 'E']),
 ('B-C', ['A', 'B', 'D', 'E']),
 ('C-D', ['A', 'B', 'D', 'E']),
 ('C-E', ['A', 'B', 'D', 'E']),
 ('A-D', ['A', 'B', 'C', 'E']),
 ('B-D', ['A', 'B', 'C', 'E']),
 ('C-D', ['A', 'B', 'C', 'E']),
 ('D-E', ['A', 'B', 'C', 'E']),
 ('B-E', ['B', 'C', 'D']),
 ('C-E', ['B', 'C', 'D']),
 ('D-E', ['B', 'C', 'D'])]

In [8]:
reduced = mapped.reduceByKey(lambda a, b: set(a) & set(b))
reduced.collect()

[('A-B', {'C', 'D'}),
 ('A-C', {'B', 'D'}),
 ('A-D', {'B', 'C'}),
 ('B-C', {'A', 'D', 'E'}),
 ('B-D', {'A', 'C', 'E'}),
 ('B-E', {'C', 'D'}),
 ('C-D', {'A', 'B', 'E'}),
 ('C-E', {'B', 'D'}),
 ('D-E', {'B', 'C'})]